## Spam Email Classifier with KNN using TF-IDF scores

1.   Assignment must be implemented in Python 3 only.
2.   You are allowed to use libraries for data preprocessing (numpy, pandas, nltk etc) and for evaluation metrics, data visualization (matplotlib etc.).
3.   You will be evaluated not just on the overall performance of the model and also on the experimentation with hyper parameters, data prepossessing techniques etc.
4.   The report file must be a well documented jupyter notebook, explaining the experiments you have performed, evaluation metrics and corresponding code. The code must run and be able to reproduce the accuracies, figures/graphs etc.
5.   For all the questions, you must create a train-validation data split and test the hyperparameter tuning on the validation set. Your jupyter notebook must reflect the same.
6.   Strict plagiarism checking will be done. An F will be awarded for plagiarism.

**Task: Given an email, classify it as spam or ham**

Given input text file ("emails.txt") containing 5572 email messages, with each row having its corresponding label (spam/ham) attached to it.

This task also requires basic pre-processing of text (like removing stopwords, stemming/lemmatizing, replacing email_address with 'email-tag', etc..).

You are required to find the tf-idf scores for the given data and use them to perform KNN using Cosine Similarity.

### Import necessary libraries

In [27]:
import nltk
import pandas as pd
import numpy as np
import re
import math
from numpy import dot
from numpy.linalg import norm
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.stem.porter import PorterStemmer
from collections import Counter
from nltk.corpus import stopwords
from sklearn.model_selection import train_test_split
nltk.download("stopwords")
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

### Load dataset

In [28]:
appreciate_data = pd.read_csv("emails.txt", sep="\t",header=None,names=["Type", "Content"])
word=list(appreciate_data["Type"])
sentence=list(appreciate_data["Content"])

after_list=list()
for text in sentence:
  text = re.sub(r"[^a-zA-Z0-9]", " ", text.lower())
  text=text.split()
  after_list.append(text)  #this list of list contains word after removing punctuations and making it lower
  #print(text)
  #text = [w for w in text if w not in stopwords.words('english')]
  #print(text)
print(after_list)




[['go', 'until', 'jurong', 'point', 'crazy', 'available', 'only', 'in', 'bugis', 'n', 'great', 'world', 'la', 'e', 'buffet', 'cine', 'there', 'got', 'amore', 'wat'], ['ok', 'lar', 'joking', 'wif', 'u', 'oni'], ['free', 'entry', 'in', '2', 'a', 'wkly', 'comp', 'to', 'win', 'fa', 'cup', 'final', 'tkts', '21st', 'may', '2005', 'text', 'fa', 'to', '87121', 'to', 'receive', 'entry', 'question', 'std', 'txt', 'rate', 't', 'c', 's', 'apply', '08452810075over18', 's'], ['u', 'dun', 'say', 'so', 'early', 'hor', 'u', 'c', 'already', 'then', 'say'], ['nah', 'i', 'don', 't', 'think', 'he', 'goes', 'to', 'usf', 'he', 'lives', 'around', 'here', 'though'], ['freemsg', 'hey', 'there', 'darling', 'it', 's', 'been', '3', 'week', 's', 'now', 'and', 'no', 'word', 'back', 'i', 'd', 'like', 'some', 'fun', 'you', 'up', 'for', 'it', 'still', 'tb', 'ok', 'xxx', 'std', 'chgs', 'to', 'send', '1', '50', 'to', 'rcv'], ['even', 'my', 'brother', 'is', 'not', 'like', 'to', 'speak', 'with', 'me', 'they', 'treat', 'me'

### Preprocess data

In [29]:
stop_word=list()
stop_word=stopwords.words("english")
#list of stop words
#print(stop_word)
temp_word=list()
#this list contains list of list after removing stop words and after removing single length word
for i in after_list:
  simple_word=list()
  for j in i:
    if j not in stop_word:
      #print(j)
      simple_word.append(j)
  #print(simple_word)
  temp_word.append(simple_word)

print(len(temp_word))
  


5572


In [30]:
#it just stemmed and lemmetize the word
stemmed_list=list()
for i in temp_word:
  lemmed = [WordNetLemmatizer().lemmatize(w) for w in i]
  #stemmed = [PorterStemmer().stem(w) for w in lemmed]
  stemmed_list.append(lemmed)
print(stemmed_list)
len(stemmed_list) 


[['go', 'jurong', 'point', 'crazy', 'available', 'bugis', 'n', 'great', 'world', 'la', 'e', 'buffet', 'cine', 'got', 'amore', 'wat'], ['ok', 'lar', 'joking', 'wif', 'u', 'oni'], ['free', 'entry', '2', 'wkly', 'comp', 'win', 'fa', 'cup', 'final', 'tkts', '21st', 'may', '2005', 'text', 'fa', '87121', 'receive', 'entry', 'question', 'std', 'txt', 'rate', 'c', 'apply', '08452810075over18'], ['u', 'dun', 'say', 'early', 'hor', 'u', 'c', 'already', 'say'], ['nah', 'think', 'go', 'usf', 'life', 'around', 'though'], ['freemsg', 'hey', 'darling', '3', 'week', 'word', 'back', 'like', 'fun', 'still', 'tb', 'ok', 'xxx', 'std', 'chgs', 'send', '1', '50', 'rcv'], ['even', 'brother', 'like', 'speak', 'treat', 'like', 'aid', 'patent'], ['per', 'request', 'melle', 'melle', 'oru', 'minnaminunginte', 'nurungu', 'vettam', 'set', 'callertune', 'caller', 'press', '9', 'copy', 'friend', 'callertune'], ['winner', 'valued', 'network', 'customer', 'selected', 'receivea', '900', 'prize', 'reward', 'claim', 'call

5572

### Split data

In [31]:
X_train, X_test, Y_train, Y_test = train_test_split(stemmed_list,word,test_size = 0.3, random_state=100)

print(len(Y_test))
#print(len(Y_train))


1672


In [32]:
tf_list=list() #this list store the tf value of stemmed X_train list
tf_dict=list()
dict_of_index=dict()
index=0
for i in X_train:
  counts=dict(Counter(i))
  length=len(i)
  list1=list()
  list2=dict()
  for j in i:
    if j in dict_of_index:
      t=1
    else:
      dict_of_index[j]=index
      index=index+1
    x=counts[j]
    list1.append(x/length)
    list2[j]=x
  tf_list.append(list1)
  tf_dict.append(list2)
    #print(j,end=" : ")
    #print(x/length)
  #print()
#print(len(tf_dict))
print(tf_list)
#print(type(tf_dict[0]))

[[0.3333333333333333, 0.3333333333333333, 0.3333333333333333], [0.5, 0.5], [0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1], [0.2, 0.2, 0.2, 0.2, 0.2], [0.045454545454545456, 0.045454545454545456, 0.09090909090909091, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.09090909090909091, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456, 0.045454545454545456], [0.25, 0.25, 0.25, 0.25], [0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625, 0.0625], [0.3333333333333333, 0.3333333333333333, 0.3333333333333333], [0.14285714285714285, 0.14285714285714285, 0.14285714285714285, 0.14285714285714285, 0.14285714285714285, 0.14285714285714285, 0.142857142857142

In [33]:
idf_list=list()    #this stores the idf value of X_train list
total_length=len(X_train)
#print(total_length)
main_dict_idf_store=dict()
for i in X_train:
  temp_list=list()
  for j in i:
    count=0
    for x in tf_dict:
      if j in x:
        count=count+1
    val=math.log(total_length/count,10)
    val=val+1
    temp_list.append(val)
    main_dict_idf_store[j]=val
  idf_list.append(temp_list)

print(idf_list)
#print(len(idf_list[0]))

[[2.5191825997203736, 2.5867432332438565, 1.9698883252514638], [3.128666609127543, 2.7045738818540173], [3.636822097587174, 2.591064607026499, 4.113943352306837, 2.5576408515395492, 2.565758741761729, 2.2447116325758607, 4.290034611362518, 3.8129133566428552, 1.7917240575729174, 4.591064607026499], [2.752215516289244, 3.3357921019231926, 2.5303667666728873, 2.6416746003815863, 3.9890046156985366], [3.128666609127543, 2.3788770026225414, 1.7917240575729174, 3.444936571348261, 2.8057347720157324, 3.085914628706593, 4.591064607026499, 2.842876580020299, 3.511883360978874, 3.511883360978874, 2.1110576640693486, 4.591064607026499, 1.7917240575729174, 2.545741628239842, 4.290034611362518, 3.549671921868274, 3.011281010409689, 3.360615685648225, 3.636822097587174, 3.477121254719662, 2.8129133566428552, 4.591064607026499], [2.565758741761729, 2.3631779024128257, 3.31231100607367, 3.31231100607367], [3.636822097587174, 2.9678153166285988, 4.290034611362518, 4.591064607026499, 2.745966567012242,

In [34]:
first=0
for i in tf_list:
  second=0
  for j in i:
    tf_list[first][second]=tf_list[first][second]*idf_list[first][second]
    second=second+1
  first=first+1
#print(tf_list)
print(tf_list)


[[0.8397275332401245, 0.8622477444146188, 0.6566294417504879], [1.5643333045637715, 1.3522869409270086], [0.3636822097587174, 0.2591064607026499, 0.4113943352306837, 0.25576408515395493, 0.25657587417617295, 0.2244711632575861, 0.4290034611362519, 0.3812913356642855, 0.17917240575729176, 0.4591064607026499], [0.5504431032578488, 0.6671584203846386, 0.5060733533345775, 0.5283349200763173, 0.7978009231397074], [0.14221211859670652, 0.10813077284647916, 0.1628840052339016, 0.1565880259703755, 0.12753339872798783, 0.14026884675939058, 0.20868475486484087, 0.1292216627281954, 0.1596310618626761, 0.1596310618626761, 0.09595716654860675, 0.20868475486484087, 0.1628840052339016, 0.11571552855635646, 0.19500157324375084, 0.1613487237212852, 0.1368764095640768, 0.1527552584385557, 0.16531009534487154, 0.15805096612362102, 0.1278596980292207, 0.20868475486484087], [0.6414396854404323, 0.5907944756032064, 0.8280777515184174, 0.8280777515184174], [0.22730138109919837, 0.18548845728928742, 0.2681271

In [35]:
X_tf_test=list()
for i in X_test:
  counts=dict(Counter(i))
  length=len(i)
  list1=list()
  for j in i:
    x=counts[j]
    list1.append(x/length)
  X_tf_test.append(list1)
print(X_tf_test)

[[0.1111111111111111, 0.1111111111111111, 0.1111111111111111, 0.1111111111111111, 0.1111111111111111, 0.1111111111111111, 0.1111111111111111, 0.1111111111111111, 0.1111111111111111], [0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1], [0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705, 0.058823529411764705], [0.16666666666666666, 0.16666666666666666, 0.16666666666666666, 0.16666666666666666, 0.16666666666666666, 0.16666666666666666], [0.125, 0.125, 0.125, 0.125, 0.125, 0.125, 0.125, 0.125], [0.3333333333333333, 0.3333333333333333, 0.3333333333333333], [0.2857142857142857, 0.14285714285714285, 0.14285714285714285, 0.2857142857142857, 0.14285714285714285, 0.14285714285714285, 0.14285714285714

In [36]:
X_idf_test=list()
for i in X_test:
  temp=list()
  for j in i:
    if j in main_dict_idf_store:
      temp.append(main_dict_idf_store[j])
    else:
      temp.append(0)
  X_idf_test.append(temp)

print(X_idf_test) 



[[3.128666609127543, 0, 4.290034611362518, 0, 0, 3.9890046156985366, 4.591064607026499, 3.8129133566428552, 0], [3.591064607026499, 4.290034611362518, 2.721832887295523, 2.6320232147054052, 3.8920946026904804, 4.290034611362518, 3.8129133566428552, 3.0725506671486116, 3.8129133566428552, 3.9890046156985366], [2.3951649546172655, 3.511883360978874, 3.549671921868274, 3.360615685648225, 3.8920946026904804, 2.448049806772404, 2.9782807503067636, 3.6879746200345553, 4.290034611362518, 3.0595856899842437, 2.591064607026499, 2.745966567012242, 4.591064607026499, 2.9008685269979857, 4.290034611362518, 2.842876580020299, 4.113943352306837], [3.6879746200345553, 3.290034611362518, 2.9678153166285988, 0, 3.229336771008906, 3.022862882959504], [4.290034611362518, 3.745966567012242, 3.477121254719662, 3.0595856899842437, 2.3580684966343455, 1.7917240575729174, 2.41208765973333, 0], [3.360615685648225, 2.161312327024091, 2.565758741761729], [1.7917240575729174, 3.511883360978874, 4.290034611362518,

In [37]:
#storing tf-idf value of test vector
first=0
for i in X_idf_test:
  second=0
  for j in i:
    X_idf_test[first][second]=j*X_tf_test[first][second]
    second=second+1
  first=first+1
#print(tf_list)
print(X_idf_test)

[[0.3476296232363936, 0.0, 0.47667051237361313, 0.0, 0.0, 0.44322273507761517, 0.5101182896696109, 0.42365703962698387, 0.0], [0.35910646070264995, 0.4290034611362519, 0.2721832887295523, 0.2632023214705405, 0.38920946026904807, 0.4290034611362519, 0.3812913356642855, 0.3072550667148612, 0.3812913356642855, 0.3989004615698537], [0.1408920561539568, 0.20658137417522787, 0.20880423069813378, 0.19768327562636617, 0.22894674133473414, 0.14400292981014143, 0.17519298531216257, 0.21693968353144444, 0.25235497713897165, 0.17997562882260257, 0.15241556511920581, 0.1615274451183672, 0.2700626239427352, 0.17063932511752858, 0.25235497713897165, 0.1672280341188411, 0.2419966677827551], [0.6146624366724258, 0.5483391018937529, 0.49463588610476644, 0.0, 0.538222795168151, 0.5038104804932506], [0.5362543264203148, 0.46824582087653027, 0.43464015683995777, 0.38244821124803047, 0.2947585620792932, 0.22396550719661468, 0.30151095746666623, 0.0], [1.1202052285494082, 0.7204374423413636, 0.85525291392057

In [38]:
total_length=len(X_train)
final_vector=np.zeros((total_length,index))
len(final_vector)
len(final_vector[0])

6641

In [39]:
#dict_of_index   dict that store all words of train and index as key
#main_idf_dict_store    dict that store all words and their tf idf value

line_no=0
for i in X_train:
  col_no=0
  for j in i:
    final_vector[line_no][dict_of_index[j]]=tf_list[line_no][col_no]
    col_no=col_no+1
  line_no=line_no+1

#final_vector[5]

In [40]:
final_test_vector=np.zeros((len(X_test),index))

In [41]:
#X_idf_test stores the tf-idf test

first=0
for i in X_test:
  second=0
  for j in i:
    if j in dict_of_index:
      final_test_vector[first][dict_of_index[j]]=X_idf_test[first][second]
      second=second+1
    else:
      second=second+1
  first=first+1

#final_test_vector



In [42]:
from numpy.linalg import norm
def euclidean_dist(final_test_vector,final_vector,k):
  error=0
  hamtrue=0
  hamfalse=0
  spamtrue=0
  spamfalse=0
  euclid_list=list()
  final_vector=np.array(final_vector)
  index_of_test=0
  for each_row_thrty in final_test_vector:
    #index_of_test=0
    key_with_index=dict()
    index=0
    list1=np.array(each_row_thrty)
    for list2 in final_vector:
      #list2=np.array(each_row_seventy)
      cosine_value = np.linalg.norm(list1 - list2)
      if cosine_value not in key_with_index:
        key_with_index[cosine_value]=list()
      key_with_index[cosine_value].append(index)
      index=index+1

    my_list=sorted(key_with_index)
    top_k_email=list()
    cnt=0
    while cnt<k:
      for i in my_list:
        for j in key_with_index[i]:
          if(cnt<k):
            top_k_email.append(j)
            cnt=cnt+1
          else:
            break
        if cnt==k:
          break
    spam_count=0
    for i in top_k_email:
      if Y_train[i]=='spam':
        spam_count=spam_count+1
    if spam_count >= (k+1)/2:
      if Y_test[index_of_test]!='spam':
        error=error+1
        spamfalse=spamfalse+1
      else:
        spamtrue=spamtrue+1
    else:
      if Y_test[index_of_test]!='ham':
        error=error+1
        hamfalse=hamfalse+1
      else:
        hamtrue=hamtrue+1
    index_of_test=index_of_test+1

  print(error)
  # temp_list1=[]
  # temp_list2=[]
  # temp_list1.append(hamtrue)   #TN
  # temp_list1.append(spamfalse)  #FP
  # temp_list2.append(hamfalse)  #FN
  # temp_list2.append(spamtrue)   #TP
  # euclid_list.append(temp_list1)
  # euclid_list.append(temp_list2)
  return error




In [43]:
k=5
error=euclidean_dist(final_test_vector,final_vector,k)
euc_error=((len(Y_test)-error)/len(Y_test))*100
print("Accuracy : ",end=" ")
print(euc_error)

155
Accuracy :  90.72966507177034


In [44]:
from scipy.spatial.distance import cityblock
def manhattan_dist(final_test_vector,final_vector,k):
  error=0
  #hamtrue=0
  #hamfalse=0
  #spamtrue=0
  #spamfalse=0
  #manhattan_list=list()
  final_vector=np.array(final_vector)
  index_of_test=0
  for each_row_thrty in final_test_vector:
    #index_of_test=0
    key_with_index=dict()
    index=0
    list1=np.array(each_row_thrty)
    for list2 in final_vector:
      #list2=np.array(each_row_seventy)
      cosine_value = cityblock(list1, list2)
      if cosine_value not in key_with_index:
        key_with_index[cosine_value]=list()
      key_with_index[cosine_value].append(index)
      index=index+1

    my_list=sorted(key_with_index)
    top_k_email=list()
    cnt=0
    while cnt<k:
      for i in my_list:
        for j in key_with_index[i]:
          if(cnt<k):
            top_k_email.append(j)
            cnt=cnt+1
          else:
            break
        if cnt==k:
          break
    ham_count=0
    for i in top_k_email:
      if Y_train[i]=='ham':
        ham_count=ham_count+1
    if ham_count >= (k+1)/2:
      if Y_test[index_of_test]!='ham':
        error=error+1
        #hamfalse=hamfalse+1
      #else:
        #hamtrue=hamtrue+1
    else:
      if Y_test[index_of_test]!='spam':
         error=error+1
         #spamfalse=spamfalse+1
      #else:
        #spamtrue=spamtrue+1
    index_of_test=index_of_test+1

  #print(error)
  #temp_l1=[]
  #temp_l1.append(hamtrue)
  #temp_l1.append(hamfalse)
  #temp_l2=[]
  #temp_l2.append(spamtrue)
  #temp_l2.append(spamfalse)
  #manhattan_list.append(temp_l1)
  #manhattan_list.append(temp_l2)
  return error



In [45]:
k=5
error=manhattan_dist(final_test_vector,final_vector,k)
man_error=((len(Y_test)-error)/len(Y_test))*100
print("Accuracy : ",end=" ")
print(man_error)


Accuracy :  90.49043062200957


In [46]:
def cos_similarity(final_test_vector,final_vector,k):
  error=0
  final_vector=np.array(final_vector)
  index_of_test=0
  hamtrue=0
  hamfalse=0
  spamtrue=0
  spamfalse=0
  cosine_sim_list=list()
  for each_row_thrty in final_test_vector:
    #index_of_test=0
    key_with_index=dict()
    index=0
    list1=np.array(each_row_thrty)
    for list2 in final_vector:
      #list2=np.array(each_row_seventy)
      cosine_value=0
      dr1=norm(list1)
      dr2=norm(list2)
      if dr1==0:
        if dr2==0:
          cosine_value=1
      else:
        if dr2!=0:
          cosine_value = dot(list1, list2)/(dr1*dr2)
      if cosine_value not in key_with_index:
        key_with_index[cosine_value]=list()
      key_with_index[cosine_value].append(index)
      index=index+1

    my_list=sorted(key_with_index,reverse=True)
    top_k_email=list()
    cnt=0
    while cnt<k:
      for i in my_list:
        for j in key_with_index[i]:
          if(cnt<k):
            top_k_email.append(j)
            cnt=cnt+1
          else:
            break
        if cnt==k:
          break
    spam_count=0
    for i in top_k_email:
      if Y_train[i]=='spam':
        spam_count=spam_count+1
    if spam_count >= (k+1)/2:
      if Y_test[index_of_test]!='spam':
        error=error+1
        spamfalse=spamfalse+1
      else:
        spamtrue=spamtrue+1
    else:
      if Y_test[index_of_test]!='ham':
        error=error+1
        hamfalse=hamfalse+1
      else:
        hamtrue=hamtrue+1
    index_of_test=index_of_test+1

  print(error)
  temp_list1=[]
  temp_list2=[]
  temp_list1.append(hamtrue)   #TN
  temp_list1.append(spamfalse)  #FP
  temp_list2.append(hamfalse)  #FN
  temp_list2.append(spamtrue)   #TP
  cosine_sim_list.append(temp_list1)
  cosine_sim_list.append(temp_list2)
  return cosine_sim_list



In [ ]:
k_value=[1,3,5,7,11,17,23,28]

accuracy_val=list()
accs=list()
for i in k_value:
  cosine_similarity_val=cos_similarity(final_test_vector,final_vector,i)
  TN=cosine_similarity_val[0][0]
  FP=cosine_similarity_val[0][1]
  FN=cosine_similarity_val[1][0]
  TP=cosine_similarity_val[1][1]

  Precision=(TN)/(TN+FN)
  acc=(TP+TN)/(TP+TN+FP+FN)
  accs.append(acc)
  print(acc)
  #Precision=(TP)/(TP+FP)
#print(Precision)
#print("Recall : ",end=" ")
  Recall=(TN)/(TN+FP)
  #Recall=(TP)/(TP+FN)
#print()
#print("F1 Score : ",end=" ")
  f_score=2*((Precision*Recall)/(Precision+Recall))
  accuracy_val.append(f_score)
#print(f_score)


### Train your KNN model (reuse previously iplemented model built from scratch) and test on your data

***1. Experiment with different distance measures [Euclidean distance, Manhattan distance, Hamming Distance] and compare with the Cosine Similarity distance results.***

In [ ]:
import matplotlib.pyplot as plt
x = np.arange(3)
plt.bar(x, height=[accs[2]*100,man_error,euc_error])
plt.xticks(x, ['cosine','manahattan','euclidean',]);

***2. Explain which distance measure works best and why? Explore the distance measures and weigh their pro and cons in different application settings.***

Among all the 3 distance measures, cosine_similarity works best with accuracy of 0.964 at k=5 because cosine similarly will mark all the documents as vectors of tf-idf tokens and measures the similarity in cosine space (the angle between the vectors).Sometimes the query length would be small but it might be closely related to the document in such cases cosine similarity is the best to find relevance.

**Cosine Similarity:**It is mainly used to find the similarity between 2 data points. As the distance between the 2 data points decreases, amount of similarity increases, and vice-versa.Cosine similarity is calculated by CosΘ and cosine distance is 1-CosΘ

**Pros:** -  

1.   Independent of document length is a very important quality of cosine similarity. As previously said, even if the query length is little but it is strongly related to other documents, cosine similarity is the best option.
2.   Both categorical and continuous variables can be used in cosine similarity.

**Cons:** - 

1.   When there are a lot of qualities to pick from, Cosine Similarity works well.
2.   In other words, cosine similarity is less ideal in low-dimensional spaces.

**Application Area:** Used for text analyses,this measure is quite frequently used when data is represented by word counts.

**Manhattan Distance:**It is calculated as sum of absolute difference between the two vectors. It is related to L1 vector norm & the sum absolute error and mean absolute error metric.

**Pros:** - 

1.   Manhattan Distance is simple to generalize to higher dimensions.
2.   It works fine when dataset has discrete or binary attribute.



**Cons:** - 

1.   It has a number of drawbacks, including the inability to apply it effectively with picture data.
2.   It is less intutive to work in higher dimensional data. It is likely to give a higher distance than euclidean as it does not account for the shortest path possible.


**Application Area**: Chess

**Euclidean Distance :**It is the distance that can be explained best as the length of segment connecting two points.

**Pros:** -  

1.   Euclidean Distance is simple to implement.
2.   It is easy to test the result.


**Cons:** -  

1.   The result is highly influenced by the variables which have larger values.

**Application Area :**Application involving Internal data, analytics of health Psychology.





***3. Report Mean Squared Error(MSE), Mean-Absolute-Error(MAE), R-squared (R2) score in a tabular form***

***4. Choose different K values (k=1,3,5,7,11,17,23,28) and experiment. Plot a graph showing R2 score vs k.***

In [ ]:
import matplotlib.pyplot as plt
plt.plot(k_value,accuracy_val)
plt.show()

### Train and test Sklearn's KNN classifier model on your data (use metric which gave best results on your experimentation with built-from-scratch model.)

In [ ]:
from sklearn.neighbors  import KNeighborsClassifier
from sklearn.metrics import f1_score
#helper functions
def train_clf(clf, X_train, y_train): 
    return clf.fit(X_train, y_train)
    
def pred_clf(clf, features, target):
    y_pred = clf.predict(features)
    return f1_score(target, y_pred, pos_label ='ham')

def train_predict(clf, X_train, y_train, X_test, y_test):
    train_clf(clf, X_train, y_train)
    return pred_clf(clf, X_test, y_test)

In [ ]:
k_vals = [1,3,5,7,11,17,23,28]

f1_score_list = list()
for k in k_vals:
  knn = KNeighborsClassifier(n_neighbors=k,metric="cosine")
  
  f1_s = train_predict(knn, final_vector, Y_train, final_test_vector, Y_test)
  f1_score_list.append(f1_s)

In [ ]:
import matplotlib.pyplot as plt
plt.plot(k_vals,f1_score_list)
plt.show()

***Compare both the models result.***

In [ ]:
print("value of diiferent k for which f1-score is calculated")
print(k_vals)
print("f1-score of sk-learn cosine function")
print(f1_score_list)
print("f1-score of my own cosine function")
print(accuracy_val)

***What is the time complexity of training using KNN classifier?***

The time complexity of training using KNN classifier is O(1).
As KNN does no training, at training phase it directly stores the complete data set but it does not do any calculations and that's why known as lazy algorithm.



***What is the time complexity while testing? Is KNN a linear classifier or can it learn any boundary?***